<h3>Exemples Folium   <br> https://python-visualization.github.io/folium/modules.html

## Table of Contents

<div  style="margin-top: 20px">

1. [Cercle 100km](#0)<br>
2. [Marker, CircleMarker, Polygonmarker, LatLngpopup](#1)<br>
3. [Importation d'un fichier Geojson](#3) <br>
4. [Cercles par arrondissement, Tailles proportionelles à la surface](#4) <br>
5. [Chloropeth](#5) <br> 
6. [Coloriage a partir de donnees](#6) <br> 
6b.[Ajout legende et titre par macro](#20) <br> 
7. [Polygon, Polyline](#7) <br> 
8. [Shapely et point dans polygon](#8) <br>   
9. [Importation du fichier des cotes 100m](#9) <br>  
10. [Analyse du geojson](#10) <br> 
11. [Connaitre le polygone associé à un point avec shapely](#11) <br>     
12. [Geojson des terres atlantique nord](#12) <br>     
13. [Verification point dans polygones](#13) <br>     
14. [Waypoints](#14) <br>     
15. [Layers](#15) <br>     
16. [Ajouter une image à une carte folium](#16) <br>     
17. [](#17) <br>     
   
</div>
<hr>

In [3]:
import os
import requests
import numpy as np
import pandas as pd
import folium
import json
import geopandas as gpd
from branca.element import Template, MacroElement
from bs4 import BeautifulSoup
from shapely.geometry import Point,Polygon
from shapely import speedups
from urllib.request import urlretrieve


In [4]:
#home
lat1=48.8043
long1=2.5945

<h3>Cercle 100 km pour confinement <a id="0"></a>

In [5]:
france = folium.Map(location=[48.85, 2.35], zoom_start=6)  # centrage sur paris
HOME = [48.804415, 2.594467]
folium.Circle(HOME,radius = 100000, fill=True, color='blue',fill_opacity=0.1 ).add_to(france)
# display world map
france

<h3> Marker, CircleMarker, Polygonmarker, LatLngpopup <a id="1"></a>

In [6]:
m = folium.Map( location=[lat1,long1],  zoom_start=13)
folium.LatLngPopup().add_to(m)   # popup lat long
folium.Marker([lat1,long1], popup='<i>Popup Home</i>', tooltip='Tooltip Home').add_to(m)

folium.CircleMarker(location=[48.8091,2.5732],radius=10,color='black',popup='Mairie').add_to(m)
folium.RegularPolygonMarker(location=[48.7933,2.5551],color='red', popup='centre commercial',fill_color='red',rotation=45, radius=50).add_to(m)  
#folium.RegularPolygon(location=[48.7933,2.5551],color='red', popup='centre commercial',fill_color='red',rotation=45, radius=50,size=1000).add_to(m)  
m

In [7]:
paris = folium.Map(location = [48.856578, 2.351828], zoom_start = 12)
folium.Marker([48.856578, 2.351828], popup = "PARIS").add_to(paris)
folium.CircleMarker([48.856578, 2.351828], popup = "Popup : PARIS",tooltip='Tooltip : Paris', radius = 50,color='black',fill_color='red',fill_opacity=0.2).add_to(paris)
paris

<h3>Importation d'un fichier Geojson <a id="3"></a>

In [8]:
url='https://opendata.paris.fr/explore/dataset/arrondissements/download/?format=geojson&timezone=Europe/Berlin&lang=fr' 
nom_fichier='arrondissements.geojson'    
urlretrieve(url, nom_fichier)  # recuperation des fichiers

print('GeoJSON file downloaded!') 
geo = json.load(open("arrondissements.geojson"))


GeoJSON file downloaded!


<h3> Analyse du fichier Geojson

In [9]:
geo.keys()

dict_keys(['type', 'features'])

In [10]:
geo["type"]

'FeatureCollection'

In [11]:
geo["features"][0]['type']

'Feature'

In [12]:
geo["features"][0]['properties']

{'n_sq_co': 750001537,
 'perimetre': 6483.68678565,
 'l_ar': '6ème Ardt',
 'surface': 2153095.58639283,
 'geom_x_y': [48.8491303586, 2.33289799905],
 'n_sq_ar': 750000006,
 'l_aroff': 'Luxembourg',
 'c_arinsee': 75106,
 'c_ar': 6}

In [13]:
#geo["features"][0]['geometry']

In [14]:
#geo["features"][0]['geometry']['coordinates']

Marqueur par arrondissement
Avec les informations contenues dans geom_x_y, nous allons pouvoir ajouter un marqueur pour chaque arrondissement, en mettant dans la popup, le nom de l'arrondissement.

In [15]:
paris_arr_marker = folium.Map(location = [48.856578, 2.351828], zoom_start = 12)
for arr in geo["features"]:
    prop = arr["properties"]
    folium.Marker(prop["geom_x_y"], popup = prop["l_ar"]).add_to(paris_arr_marker)
paris_arr_marker

<h4>Cercles par arrondissement, Tailles proportionelles à la surface <a id="4"></a>


In [16]:
paris_arr_circle = folium.Map(location = [48.856578, 2.351828], zoom_start = 12)
for arr in geo["features"]:
    prop = arr["properties"]
    folium.CircleMarker(prop["geom_x_y"],color='black', fill_color='black',fill_opacity=0.3,
                        popup = prop["l_ar"],
                        radius = prop["surface"] / 1000000).add_to(paris_arr_circle)
paris_arr_circle

<h3>Chloropeth <a id="5"></a>

In [17]:
paris = folium.Map(location = [48.856578, 2.351828], zoom_start = 12)
paris.choropleth(geo_data = geo, fill_color='red' ,fill_opacity=0.3 )
paris

/home/jphe/anaconda3/lib/python3.7/site-packages/folium/folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


<h3>Coloriage a partir de donnees <a id="6"></a>

In [18]:
df = pd.DataFrame({
    "Arrondissement" : [arr["properties"]["c_ar"] for arr in geo["features"]], 
    "Surface" : [arr["properties"]["surface"] for arr in geo["features"]]
})
df.head()

Arrondissement       Surface
0               6  2.153096e+06
1               9  2.178303e+06
2              18  5.996051e+06
3               4  1.600586e+06
4              14  5.614877e+06

In [19]:
paris.choropleth(
    geo_data=geo,
    name='Taille',
    data=df,
    columns=['Arrondissement', 'Surface'],
    key_on='feature.properties.c_ar',                           # donnee recuperee dans geo["features"][0]['properties']
    fill_color='YlOrRd', 
    #fill_color='YlGn',
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name='Surface par arrondissement'
)
paris

<h3>metro et rer

In [20]:
url='https://data.iledefrance-mobilites.fr/explore/dataset/emplacement-des-gares-idf/download/?format=csv&timezone=Europe/Berlin&lang=fr&use_labels_for_header=true&csv_separator=%3B'
da = pd.read_csv(url,sep=';')
da.head(2)  
    

Geo Point  \
0  48.8701642009,2.35049797186   
1   48.8407450152,2.2285369815   

                                           Geo Shape  OBJECTID  id_ref_zdl  \
0  {"type": "Point", "coordinates": [2.3504979718...         2       45100   
1  {"type": "Point", "coordinates": [2.2285369815...         7       42381   

   gares_id                      nom_gare                       nomlong  \
0        91                Bonne Nouvelle                BONNE NOUVELLE   
1       100  Boulogne-Pont de Saint-Cloud  BOULOGNE-PONT DE SAINT CLOUD   

                         nom_iv  num_mod  mode_  ...  res_com  cod_resf  \
0                Bonne Nouvelle     2240  Metro  ...       M9       3.0   
1  Boulogne-Pont de Saint-Cloud     2263  Metro  ...      M10       3.0   

   res_stif  exploitant  num_psr  idf  principal            x             y  \
0     110.0        RATP        0    1          0  652356.5489  6.863545e+06   
1     110.0        RATP        0    1          0  643378.5475  6.860354e+06   

                                         picto ligne  
0  https://data.iledefrance-mobilites.fr/api/v2/c...  
1  https://data.iledefrance-mobilites.fr/api/v2/c...  

[2 rows x 41 columns]

<h3>Cleaning

In [21]:
cols=['Geo Point',   'nom_gare', 'mode_', 'ligne']
da = da[cols]
da.head(2)

Geo Point                      nom_gare  mode_ ligne
0  48.8701642009,2.35049797186                Bonne Nouvelle  Metro     9
1   48.8407450152,2.2285369815  Boulogne-Pont de Saint-Cloud  Metro    10

<h3>Only metro and RER

In [22]:
db=da.loc[da['mode_'].isin(['Metro','RER']),:]
db.head(2)

Geo Point                      nom_gare  mode_ ligne
0  48.8701642009,2.35049797186                Bonne Nouvelle  Metro     9
1   48.8407450152,2.2285369815  Boulogne-Pont de Saint-Cloud  Metro    10

<h3> Splitting coords

In [23]:
dc=db['Geo Point'].str.split(",", expand=True)
db=db.join(dc)
db.rename(columns={'nom_gare':'gare','mode_':'type',0:'Latitude',1:'Longitude'},inplace=True)
db=db.astype({'Latitude': float, 'Longitude':float})
db.drop(['Geo Point'], axis=1,inplace=True)
db.head(2)

gare   type ligne   Latitude  Longitude
0                Bonne Nouvelle  Metro     9  48.870164   2.350498
1  Boulogne-Pont de Saint-Cloud  Metro    10  48.840745   2.228537

<h3>Fetching Polygone Val de marne <a id="2"></a>

In [24]:
#url='https://raw.githubusercontent.com/gregoiredavid/france-geojson/master/departements-version-simplifiee.geojson'
url='https://raw.githubusercontent.com/gregoiredavid/france-geojson/master/departements.geojson'
nom_fichier='departements.json'    
urlretrieve(url, nom_fichier)  # recuperation des fichiers
print('GeoJSON file downloaded!') 

GeoJSON file downloaded!


In [25]:
geo = json.load(open("departements.json"))
geo["features"][94]['properties']['nom']

'Val-de-Marne'

In [26]:
contour=geo["features"][94]['geometry']['coordinates'][0]
#inversion des coordonnees pour cartographie polyline
cont_xy=[]
for i in range (len(contour)):
    cont_xy.append([contour[i][1],contour[i][0]])
polygone_94=Polygon(contour)


In [27]:
def in_poly (x,y,poly):
    point=Point([x,y])
    if point.within(poly):
        r=1
    else:
        r=0
    return r

<h3>Restriction to Val de Marne

In [28]:
db['Z'] = db.apply(lambda row: in_poly(row['Longitude'], row['Latitude'],polygone_94), axis=1)
db.head(2)

gare   type ligne   Latitude  Longitude  Z
0                Bonne Nouvelle  Metro     9  48.870164   2.350498  0
1  Boulogne-Pont de Saint-Cloud  Metro    10  48.840745   2.228537  0

In [29]:
db=db[db['Z']==1]
db=db.reset_index(drop=True)
db.head(55)
db.shape

(53, 6)

<h3>Splitting Metro and RER 

In [30]:
dmetro=db[db['type']=='Metro']
dmetro.head()

gare   type ligne   Latitude  Longitude  Z
0                               Bérault  Metro     1  48.845471   2.429205  1
1                    Créteil-Université  Metro     8  48.789978   2.450453  1
2                Villejuif-Louis Aragon  Metro     7  48.787563   2.367804  1
10  École Vétérinaire de Maisons-Alfort  Metro     8  48.814803   2.422376  1
11                     Charenton-Écoles  Metro     8  48.821596   2.413738  1

In [31]:
drer=db[db['type']=='RER']
drer.head()

gare type  ligne   Latitude  Longitude  Z
3               BRY-SUR-MARNE  RER  RER A  48.844901   2.525923  1
4               CHOISY-LE-ROI  RER  RER C  48.763787   2.411387  1
5                    GENTILLY  RER  RER B  48.815230   2.340891  1
6       LE PARC-DE-SAINT-MAUR  RER  RER A  48.805378   2.486350  1
7  MAISONS-ALFORT-ALFORTVILLE  RER  RER D  48.802049   2.426482  1

In [32]:
template = """
{% macro html(this, kwargs) %}

<!doctype html>
<html lang="en">
<head>
  <meta charset="utf-8">
  <meta name="viewport" content="width=device-width, initial-scale=1">
  <title>jQuery UI Draggable - Default functionality</title>
  <link rel="stylesheet" href="//code.jquery.com/ui/1.12.1/themes/base/jquery-ui.css">

  <script src="https://code.jquery.com/jquery-1.12.4.js"></script>
  <script src="https://code.jquery.com/ui/1.12.1/jquery-ui.js"></script>
  
  <script>
  $( function() {
    $( "#maplegend" ).draggable({
                    start: function (event, ui) {
                        $(this).css({
                            right: "auto",
                            top: "auto",
                            bottom: "auto"
                        });
                    }
                });
                
       $( "#titlebox" ).draggable({
                    start: function (event, ui) {
                        $(this).css({
                            right: "auto",
                            top: "auto",
                            bottom: "auto"
                        });
                    }
                });
                          
                
});

  </script>
</head>
<body>

<div id= 'titlebox' class='titlebox' style='position: absolute; z-index:9998; border:2px solid grey; background-color:rgba(255, 255, 255, 0.8);
     border-radius:6px; padding: 10px; font-size:14px; left: 100px; top: 20px;'>
 
 <div id= 'title' class='title'>
 Metro and RER Stations 
</div>
</div>


 
<div id='maplegend' class='maplegend' 
    style='position: absolute; z-index:9999; border:2px solid grey; background-color:rgba(255, 255, 255, 0.8);
     border-radius:6px; padding: 10px; font-size:14px; right: 20px; bottom: 20px;'>
     
<div class='legend-title'>Legend </div>
<div class='legend-scale'>
  <ul class='legend-labels'>
    <li><span style='background:black;opacity:0.7; border-radius:8px'></span> Metro</li>
    <li><span style='background:green;opacity:0.7; border-radius:8px'></span> RER</li>
   
  </ul>
</div>
</div>
 
</body>
</html>

<style type='text/css'>

  .titlebox{text-align: center;
    width :300px;
    height :50px;
    margin-bottom: 5px;
    font-weight: bold;
    font-size: 100%;}

 .titlebox .title
     {text-align: center;
   
    font-weight: bold;
    font-size: 100%;}

  .maplegend .legend-title {
    text-align: left;
    margin-bottom: 5px;
    font-weight: bold;
    font-size: 90%;
    }
  .maplegend .legend-scale ul {
    margin: 0;
    margin-bottom: 5px;
    padding: 0;
    float: left;
    list-style: none;
    }
  .maplegend .legend-scale ul li {
    font-size: 80%;
    list-style: none;
    margin-left: 0;
    line-height: 18px;
    margin-bottom: 2px;
    }
  .maplegend ul.legend-labels li span {
    display: block;
    float: left;
    height: 16px;
    width: 16px;
    border-radius:4px
    margin-right: 5px;
    margin-left: 0;
    border: 1px solid #999;
    }
  .maplegend .legend-source {
    font-size: 80%;
    color: #777;
    clear: both;
    }
  .maplegend a {
    color: #777;
    }
</style>
{% endmacro %}"""

macro = MacroElement()
macro._template = Template(template)


<h3>Map<a id="3"></a>

In [33]:
m = folium.Map(location=[48.780,2.47],zoom_start=11)
folium.LatLngPopup().add_to(m)
for i,row in drer.iterrows():
    folium.Circle(location=[row["Latitude"],row["Longitude"]],radius=200,color='green', fill=True,fill_color='green',fill_opacity=0.2).add_to(m)
for i,row in dmetro.iterrows():
    folium.Circle(location=[row["Latitude"],row["Longitude"]],radius=200,color='black',fill=True,fill_color='black',fill_opacity=0.2 ).add_to(m) 
folium.PolyLine(cont_xy,color='blue', popup='Val de Marne').add_to(m)  
m.get_root().add_child(macro)  
m

<h3> Ajout legende et titre par macro <a id="20"></a>

In [34]:
template = """
{% macro html(this, kwargs) %}

<!doctype html>
<html lang="en">
<head>
  <meta charset="utf-8">
  <meta name="viewport" content="width=device-width, initial-scale=1">
  <title>jQuery UI Draggable - Default functionality</title>
  <link rel="stylesheet" href="//code.jquery.com/ui/1.12.1/themes/base/jquery-ui.css">

  <script src="https://code.jquery.com/jquery-1.12.4.js"></script>
  <script src="https://code.jquery.com/ui/1.12.1/jquery-ui.js"></script>
  
  <script>
  $( function() {
    $( "#maplegend" ).draggable({
                    start: function (event, ui) {
                        $(this).css({
                            right: "auto",
                            top: "auto",
                            bottom: "auto"
                        });
                    }
                });
                
       $( "#titlebox" ).draggable({
                    start: function (event, ui) {
                        $(this).css({
                            right: "auto",
                            top: "auto",
                            bottom: "auto"
                        });
                    }
                });
                          
                
});

  </script>
</head>
<body>

<div id= 'titlebox' class='titlebox' style='position: absolute; z-index:9998; border:2px solid grey; background-color:rgba(255, 255, 255, 0.8);
     border-radius:6px; padding: 10px; font-size:14px; left: 100px; top: 20px;'>
 
 <div id= 'title' class='title'>
 Metro and RER Stations 
</div>
</div>


 
<div id='maplegend' class='maplegend' 
    style='position: absolute; z-index:9999; border:2px solid grey; background-color:rgba(255, 255, 255, 0.8);
     border-radius:6px; padding: 10px; font-size:14px; right: 20px; bottom: 20px;'>
     
<div class='legend-title'>Legend </div>
<div class='legend-scale'>
  <ul class='legend-labels'>
    <li><span style='background:black;opacity:0.7; border-radius:8px'></span> Metro</li>
    <li><span style='background:green;opacity:0.7; border-radius:8px'></span> RER</li>
   
  </ul>
</div>
</div>
 
</body>
</html>

<style type='text/css'>

  .titlebox{text-align: center;
    width :300px;
    height :50px;
    margin-bottom: 5px;
    font-weight: bold;
    font-size: 100%;}

 .titlebox .title
     {text-align: center;
    font-weight: bold;
    font-size: 100%;}

  .maplegend .legend-title {
    text-align: left;
    margin-bottom: 5px;
    font-weight: bold;
    font-size: 90%;
    }
  .maplegend .legend-scale ul {
    margin: 0;
    margin-bottom: 5px;
    padding: 0;
    float: left;
    list-style: none;
    }
  .maplegend .legend-scale ul li {
    font-size: 80%;
    list-style: none;
    margin-left: 0;
    line-height: 18px;
    margin-bottom: 2px;
    }
  .maplegend ul.legend-labels li span {
    display: block;
    float: left;
    height: 16px;
    width: 16px;
    border-radius:4px
    margin-right: 5px;
    margin-left: 0;
    border: 1px solid #999;
    }
  .maplegend .legend-source {
    font-size: 80%;
    color: #777;
    clear: both;
    }
  .maplegend a {
    color: #777;
    }
</style>
{% endmacro %}"""

macro = MacroElement()
macro._template = Template(template)

In [35]:
m = folium.Map(location=[48.780,2.47],zoom_start=11)
folium.LatLngPopup().add_to(m)
#for i,row in drer.iterrows():
#    folium.Circle(location=[row["Latitude"],row["Longitude"]],radius=200,color='green', fill=True,fill_color='green',fill_opacity=0.2).add_to(m)
#for i,row in dmetro.iterrows():
#    folium.Circle(location=[row["Latitude"],row["Longitude"]],radius=200,color='black',fill=True,fill_color='black',fill_opacity=0.2 ).add_to(m) 
folium.PolyLine(cont_xy,color='blue', popup='Val de Marne').add_to(m)  
m.get_root().add_child(macro)  
m

In [37]:
template = """
{% macro html(this, kwargs) %}

<html>
<head>
<style type='text/css'>
    h4{
    color:'red';
    font-weight: bold;
    font-size: 100%;}
  </style>
</head>
<body>
<div id= 'titlebox'  style='position: absolute; z-index:9998; border:2px solid black; background-color:rgba(255, 255, 255, 0.8);
     border-radius:6px; padding: 10px; font-size:14px; left: 100px; top: 20px;'>
     <div  >
         <h4 style ='color:red;' '>Essai de Html </h4>
         <form action ="#" method="post">
             Longitude <input type="text" value = 5 name ="long"><br>
             Latitude .. <input type="text" value = 10 name ="lat"><br> 
            
             <input type="submit" value ="submit">
       
         </form>
     </div>
</div>

<script>alert ('message') </script>
</body>

</html>
{% endmacro %}"""

macro = MacroElement()
macro._template = Template(template)
m = folium.Map(location=[48.780,2.47],zoom_start=11)
folium.LatLngPopup().add_to(m)
folium.PolyLine(cont_xy,color='blue', popup='Val de Marne').add_to(m)  
m.get_root().add_child(macro)
#filepath = '~\map.html'
#m.save(filepath)
m

<h3>Polygon, Polyline <a id="7"></a>

In [38]:
contour1=[[0, 20], [0, 40], [20, 40], [20, 20],[30, 45], [0, 20]]
contour2=[[-10, 20], [0, 40], [-20, 40], [-20, 20],[-30, 45], [-10, 20]]
paris = folium.Map(location = [-10, 30], zoom_start = 3)

folium.Polygon(contour1,color='red', popup='centre commercial',fill_color='red',rotation=45, radius=50).add_to(paris)  
folium.PolyLine(contour2,color='blue', popup='centre commercial',rotation=45, radius=50).add_to(paris)  
paris

<h3>Shapely et point dans polygone <a id="8"></a>

In [39]:
from shapely.geometry import Point,Polygon
from shapely import speedups

def in_poly (x,y,poly):
    point=Point([x,y])
    if point.within(poly):
        r=1
    else:
        r=0
    return r

<h3>Importation du fichier des cotes 100m <a id="9"></a>

In [40]:
#url='https://github.com/simonepri/geo-maps/releases/latest/download/earth-lands-100m.geo.json'
url='https://github.com/simonepri/geo-maps/releases/latest/download/earth-seas-5km.geo.json'
nom_fichier='cotes_5km.json' 
url='https://github.com/simonepri/geo-maps/releases/latest/download/earth-seas-2km5.geo.json'
nom_fichier='cotes_2km5.json' 
url='https://github.com/simonepri/geo-maps/releases/latest/download/earth-seas-500m.geo.json'

    #url='https://github.com/simonepri/geo-maps/releases/latest/download/earth-lands-2km5.geo.json'
#nom_fichier='cotes_2km.json' 
#url='https://opendata.paris.fr/explore/dataset/arrondissements/download/?format=geojson&timezone=Europe/Berlin&lang=fr'    
urlretrieve(url, nom_fichier)  # recuperation des fichiers
print('GeoJSON file downloaded!') 

GeoJSON file downloaded!


In [41]:
geo = json.load(open("cotes_2km5.json"))
monde = folium.Map(location = [48.856578, 2.351828], zoom_start = 7)
folium.LatLngPopup().add_to(monde)   # popup lat long
monde.choropleth(geo_data = geo, fill_color='blue' ,fill_opacity=0.05 )
folium.Marker([-29, 28], popup = "Test_a_terre").add_to(monde)
folium.Marker([0, 70], popup = "Test_en mer").add_to(monde)
#monde

<h3>Analyse du geojson <a id="10"></a>

In [42]:
#print     (geo["geometries"][0]["coordinates"][0][0])  # coordonnees du ploygone 0
#for i in range (len (geo["geometries"][0]["coordinates"][0])):
   # print (i,len(geo["geometries"][0]["coordinates"][0][i]))


In [43]:

n=0
monde = folium.Map(location = [43, 27], zoom_start = 2)
folium.LatLngPopup().add_to(monde)   # popup lat long
contour=geo["geometries"][0]["coordinates"][0][n]
cont_xy=[]
for i in range (len(contour)):
    cont_xy.append([contour[i][1],contour[i][0]])
    
a= Polygon(geo["geometries"][0]["coordinates"][0][n])

folium.Marker([-29, 28], popup = "Test_a_terre").add_to(monde)
folium.Marker([0, 70], popup = "Test_en mer").add_to(monde)
folium.PolyLine(cont_xy,color='blue', popup='ligne de cotes').add_to(monde)  

monde

In [44]:
import pickle

In [45]:
len(geo["geometries"][0]["coordinates"][0])  # nombre de polygones

28670

In [46]:
def in_poly (x,y,poly):
    point=Point([x,y])
    if point.within(poly):
        r=1
    else:
        r=0
    return r

monde = folium.Map(location = [43, 27], zoom_start = 2)

for j in range (20):
    contour=geo["geometries"][0]["coordinates"][0][j]
    cont_xy=[]
    for i in range (len(contour)):
        cont_xy.append([contour[i][1],contour[i][0]])   
    folium.PolyLine(cont_xy,color='blue', popup='ligne de cotes').add_to(monde) 
    
    
    
#for item in (geo["geometries"][0]["coordinates"]) :
#    print (len(item))
    
#print     (geo["geometries"][0]["coordinates"][0][0])
a= Polygon(geo["geometries"][0]["coordinates"][0][683])   # afrique
                                                  

folium.LatLngPopup().add_to(monde)   # popup lat long                                                 

folium.PolyLine(cont_xy,color='blue', popup='ligne de cotes').add_to(monde)  



folium.Marker([-29, 28], popup = "Test_a_terre").add_to(monde)
folium.Marker([0, 70], popup = "Test_en mer").add_to(monde)
folium.Marker([-29.51, 31.19], popup = "Test_en mer").add_to(monde)
folium.Marker([-16, -43], popup = "amerique").add_to(monde)


point1=Point(28,-29)
point2=Point(70,0)
point3=Point(31.19,-29.51)
if point1.within(a):
    print ("le point 1 est en afrique" )
else:
    print ("le point 1 est en mer")
    
if point2.within(a):
    print ("le point 2 est en afrique" )
else:
    print ("le point 2 est en mer")    

    
if point3.within(a):
    print ("le point 3 est en afrique" )
else:
    print ("le point 3 est en mer")    

monde

le point 1 est en mer
le point 2 est en mer
le point 3 est en mer


<h3>Connaitre le polygone associé à un point avec shapely <a id="11"></a>

In [47]:
point1=Point(28,-29)
point1=Point(46.77,-19.56)   
monde = folium.Map(location = [43, 27], zoom_start = 2)

folium.LatLngPopup().add_to(monde)   # popup lat long    
folium.Marker([-29, 28], popup = "Test_a_terre").add_to(monde)

# on parcourt les polygones
for i in range (len (geo["geometries"][0]["coordinates"][0])):
    #print (i,len(geo["geometries"][0]["coordinates"][0][i]))
    a= Polygon(geo["geometries"][0]["coordinates"][0][i])
    if point1.within(a): 
        print ("le point 1 est dans le polygone",i )
        k=i
        
contour=geo["geometries"][0]["coordinates"][0][k]
cont_xy=[]
for i in range (len(contour)):
    cont_xy.append([contour[i][1],contour[i][0]])   
folium.PolyLine(cont_xy,color='blue', popup='ligne de cotes').add_to(monde)         
monde        

le point 1 est dans le polygone 0
le point 1 est dans le polygone 22939


<h3>Geojson des terres atlantique nord <a id="12"></a>

In [48]:
print((atlantique["features"][0]["geometry"]["coordinates"][0]))

NameError: name 'atlantique' is not defined

In [49]:
liste=[]
for j in range(len((atlantique["features"][0]["geometry"]["coordinates"]))):
    a=(atlantique["features"][0]["geometry"]["coordinates"][j])         
    point1=Point(a[0],a[1])
    #print (point1)
    # on parcourt les polygones
    for i in range (len (geo["geometries"][0]["coordinates"][0])):
        #print (i,len(geo["geometries"][0]["coordinates"][0][i]))
        a= Polygon(geo["geometries"][0]["coordinates"][0][i])
        if point1.within(a):
            k=i
            #print ("le point 1 est dans le polygone",k )
            if k>0:
                liste.append(k)
print (liste)                
    
    

NameError: name 'atlantique' is not defined

<h3>Verification point dans polygones <a id="13"></a>

In [50]:
point = Point(-2.25, 47.67)
print (point.x)
monde = folium.Map(location = [43, 27], zoom_start = 2)
folium.LatLngPopup().add_to(monde)   # popup lat long   
folium.Marker([point.y,point.x], popup = "Test_a_terre").add_to(monde)

for i in liste:
    a= Polygon(geo["geometries"][0]["coordinates"][0][i])
    if point.within(a):
        print ("le point est dans les terres", i)
        break
monde

-2.25


In [51]:
contour= geo["geometries"][0]["coordinates"][0][0]
del contour[1:178]
monde = folium.Map(location = [43, 27], zoom_start = 2)
folium.LatLngPopup().add_to(monde)   # popup lat long                                                 

cont_xy=[]
for i in range (len(contour)):
    cont_xy.append([contour[i][1],contour[i][0]])   
folium.PolyLine(cont_xy,color='blue', popup='ligne de cotes').add_to(monde)
folium.Marker(cont_xy[0],color='blue', popup='ligne de cotes').add_to(monde)
folium.Marker(cont_xy[178],color='red', popup='ligne de cotes').add_to(monde)


monde 

<h3> Waypoints <a id="14"></a>

In [52]:
m = folium.Map(location=[48.856578, 2.351828], zoom_start = 12)
m.add_child(folium.ClickForMarker(popup='Waypoint'))
m.add_child(folium.LatLngPopup())
m

<h3>Layers <a id="15"></a>

In [53]:
m = folium.Map(location=[48.856578, 2.351828], zoom_start = 12)
val_de_marne = 'val_de_marne.json'
paris='arrondissements.geojson'

folium.GeoJson(
    val_de_marne,
    name='val de marne'
).add_to(m)

folium.GeoJson(
    paris,
    name='paris',
).add_to(m)

folium.LayerControl().add_to(m)

m

<h3> Ajouter une image à une carte folium <a id="16"></a>

In [54]:
m = folium.Map([37, 0], zoom_start=2, tiles='stamentoner')

folium.raster_layers.ImageOverlay(
    image='https://upload.wikimedia.org/wikipedia/commons/f/f4/Mercator_projection_SW.jpg',
    name='I am a jpeg',
    bounds=[[-82, -180], [82, 180]],
    opacity=0.3,
    interactive=False,
    cross_origin=False,
    zindex=1,
    alt='Wikipedia File:Mercator projection SW.jpg'
).add_to(m)

folium.LayerControl().add_to(m)


#m.save(os.path.join('results', 'ImageOverlay_1.html'))

m

In [55]:


import numpy as np
image = np.zeros((61, 61))
image[0, :] = 1.0
image[60, :] = 1.0
image[:, 0] = 1.0
image[:, 60] = 1.0


m = folium.Map([37, 0], zoom_start=2)

folium.raster_layers.ImageOverlay(
    image=image,
    bounds=[[0, -60], [60, 60]],
    colormap=lambda x: (1, 0, 0, x),
).add_to(m)

m

In [56]:
m = folium.Map([37, 0], zoom_start=3)
folium.LatLngPopup().add_to(m)   # popup lat long   
image=('image2.jpeg')
folium.raster_layers.ImageOverlay(
    image=image,
    bounds=[[20, -30], [50, 30]]     # [[lat_min, lon_min], [lat_max, lon_max]]
   
).add_to(m)

m

<h3> Incorporation video

In [57]:


url='https://youtu.be/xcJtL7QggTI'


m = folium.Map([37, 0], zoom_start=2, )

folium.raster_layers.VideoOverlay(
    video_url=url,
    bounds=[[-82, -180], [82, 180]],
    autoplay=True,
    show=True,
    loop=True
   
).add_to(m)

folium.LayerControl().add_to(m)


#m.save(os.path.join('results', 'ImageOverlay_1.html'))

m


    <h3>Incorporation javascript

In [58]:
from branca.element import Element

m = folium.Map([37, 0], zoom_start=2 )
map_id = m.get_name()

my_js = """var lastZoom;
     {0}.on('zoomend', function() {
    var zoom = {0}.getZoom();
if (zoom < tooltipThreshold && (!lastZoom || lastZoom >= tooltipThreshold)) {
    {0}.eachLayer(function(l) {
        if (l.getTooltip()) {
            var tooltip = l.getTooltip();
            l.unbindTooltip().bindTooltip(tooltip, {
                permanent: false
            })
        }
    })
} else if (zoom >= tooltipThreshold && (!lastZoom || lastZoom < tooltipThreshold)) {
    {0}.eachLayer(function(l) {
        if (l.getTooltip()) {
            var tooltip = l.getTooltip();
            l.unbindTooltip().bindTooltip(tooltip, {
                permanent: true
            })
        }
    });
}
lastZoom = zoom;
})"""

e = Element(my_js)
html = m.get_root()
html.script.get_root().render()
# Insert new element or custom JS
html.script._children[e.get_name()] = e
m
#m.save('mymap.html')